# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. 

In [49]:
####install gpcam here if you do not have already done so
#!pip install gpcam==8.0.0

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [50]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [51]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [52]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run
### The following function are optional and already show you some advanced features

In [53]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    #but is just here as an example. 'acq_funciton="ucb"' will give you the same result
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * np.sqrt(cov)

def optional_mean_func(x,hyperparameters,gp_obj):
    #the prior mean function should return a vector: a mean function evaluation for every x
    return np.zeros((len(x)))

def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n

def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just needs a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this function is not needed.
    #In this example we just return the old parameters, but print the costs. 
    #I hope it is clear how the parameters can be fitted to the recorded costs.
    print("recorded costs (from,to,costs): ", costs)
    
    return parameters

In [60]:
import time
from gpcam import AutonomousExperimenterGP

def instrument(data):
    print("Suggested by gpCAM: ")
    for entry in data:
        print("suggested:", entry["x_data"])
        entry["y_data"] = np.sin(np.linalg.norm(entry["x_data"]))
        entry["cost"]  = [np.array([0,0]),entry["x_data"],np.sum(entry["x_data"])]
        print("received: ", entry["y_data"])
    print("")
    return data

#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),
                                 np.ones((3)), np.array([[0.001,100.],[0.001,100.],[0.001,100.]]),
                                 init_dataset_size= 20, instrument_func = instrument,
                                 acquisition_function = optional_acq_func, 
                                 cost_function = optional_cost_function, 
                                 cost_update_function = optional_cost_update_function,
                                 cost_function_parameters={"offset": 5.0,"slope":10.0},
                                 kernel_func = None, store_inv = True,
                                 prior_mean_func = optional_mean_func,
                                 communicate_full_dataset = False, ram_economy = True)#, info = False, prior_mean_func = optional_mean_func)


print("length of the dataset: ",len(my_ae.x_data))


#my_ae.train_async()                 #train asynchronously
my_ae.train(method = "global")       #or not, or both, choose between "global","local" and "hgdl"

Suggested by gpCAM: 
suggested: [4.17041190e-03 9.46256138e+00]
received:  -0.037775343415356356
suggested: [3.66909825 8.74423546]
received:  -0.058012642374264456
suggested: [5.94510453 6.68843303]
received:  0.45828823595898216
suggested: [0.46938763 7.09153162]
received:  0.7337762609727928
suggested: [7.48811791 1.96313816]
received:  0.9936443010391712
suggested: [9.69448689 7.87285761]
received:  -0.07769890015144432
suggested: [3.03752843 7.56117195]
received:  0.9569447699588031
suggested: [9.70415209 9.35732357]
received:  0.7921715771012081
suggested: [7.05958444 7.42870568]
received:  -0.7334030815613277
suggested: [6.77541024 1.16630315]
received:  0.5579176160910355
suggested: [2.22213423 0.39785382]
received:  0.7733594404585172
suggested: [1.05384228 8.01976067]
received:  0.9725787716060651
suggested: [3.89561468 9.22493579]
received:  -0.5555092544751437
suggested: [5.19436921 5.42547602]
received:  0.9418040480563862
suggested: [6.48320254 9.73390131]
received:  -0.7

In [61]:
#update hyperparameters in case they are optimized asynchronously
my_ae.update_hps()
print(my_ae.gp_optimizer.hyperparameters)

[0.63391923 2.27607036 1.91553794]


In [62]:
#training and client can be killed if desired and in case they are optimized asynchronously
my_ae.kill_training()

## Let's see what our initial model looks like

In [63]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x_data,my_ae.y_data]))

## Let's run the autonomus loop to 100 points

In [64]:
#run the autonomous loop
my_ae.go(N = 100, 
            retrain_async_at=[30,40,50,60,70,80,90],
            retrain_globally_at = [20,22,24,26,28,30,40,50,60,70],
            retrain_locally_at = [21,22,56,78],
            acq_func_opt_setting = lambda number: "global" if number % 2 == 0 else "local",
            update_cost_func_at = (50,),
            training_opt_max_iter = 20,
            training_opt_pop_size = 10,
            training_opt_tol      = 1e-6,
            acq_func_opt_max_iter = 20,
            acq_func_opt_pop_size = 20,
            acq_func_opt_tol      = 1e-6,
            number_of_suggested_measurements = 1,
            acq_func_opt_tol_adjust = 0.1)

Suggested by gpCAM: 
suggested: [9.71369392 1.03680205]
received:  -0.33734144644537367

Suggested by gpCAM: 
suggested: [8.69387007 1.03680301]
received:  0.6204397129561404

Suggested by gpCAM: 
suggested: [0.05179443 0.00839327]
received:  0.052446018224102976

Suggested by gpCAM: 
suggested: [7.27660116 6.56365388]
received:  -0.36602700222736234

Suggested by gpCAM: 
suggested: [3.73129106 0.96845629]
received:  -0.6543566643134934

Suggested by gpCAM: 
suggested: [6.35830985 6.92161738]
received:  0.026004295499014726

Suggested by gpCAM: 
suggested: [6.70411062 3.72150554]
received:  0.9827127252618237

Suggested by gpCAM: 
suggested: [ 8.68257606 10.        ]
received:  0.6264651839239064

Suggested by gpCAM: 
suggested: [0.4051734  2.95724194]
received:  0.15608245986553143

Suggested by gpCAM: 
suggested: [0.73354654 1.57073334]
received:  0.9867802440724345

Suggested by gpCAM: 
suggested: [2.15450421 6.71426227]
received:  0.6949016107884175

Suggested by gpCAM: 
suggested:

Suggested by gpCAM: 
suggested: [ 8.38688897 10.        ]
received:  0.4662636616801366

Suggested by gpCAM: 
suggested: [7.62909616 1.27216974]
received:  0.9928631100237428

Suggested by gpCAM: 
suggested: [7.62909604 1.27217642]
received:  0.9928632270932751

Suggested by gpCAM: 
suggested: [4.58743224 7.04150167]
received:  0.8525129227070254

Suggested by gpCAM: 
suggested: [5.21826418 2.58263655]
received:  -0.444655426368258

Suggested by gpCAM: 
suggested: [0.02303924 7.80378318]
received:  0.9987420283186917

Suggested by gpCAM: 
suggested: [0.54241797 3.5043275 ]
received:  -0.39352744695892655

Suggested by gpCAM: 
suggested: [0.78899672 0.98809091]
received:  0.9534424733911869

Suggested by gpCAM: 
suggested: [0.         7.33148778]
received:  0.8665773374375058

Suggested by gpCAM: 
suggested: [7.67290718 2.63981379]
received:  0.9663040087747177

Suggested by gpCAM: 
suggested: [7.67290574 0.        ]
received:  0.9836505060631943

Suggested by gpCAM: 
suggested: [1.3789






## Now let's plot the posterior mean after the experiment has concluded

In [45]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x_data,my_ae.y_data]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [46]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("./data/sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [47]:
from gpcam import AutonomousExperimenterFvGP

def instrument(data, instrument_dict = {}):
    for entry in data:
        print("Suggested by gpCAM: ", entry["x_data"])
        entry["y_data"] = griddata(x,y,entry["x_data"],method = "nearest", fill_value = 0)[0]
        entry["output positions"] = np.array([[0],[1]])
        print("received: ", entry["y_data"])
    print("")
    return data

def acq_func(x,obj):
    #multi-tast autonomous experiments should make use of a user-defined acquisition function to
    #make full use of the surrogate and the uncertainty in all tasks.
    a = 3.0 #3.0 for ~95 percent confidence interval
    x = np.block([[x,np.zeros((len(x))).reshape(-1,1)],[x,np.ones((len(x))).reshape(-1,1)]]) #for task 0 and 1
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    #it takes a little bit of wiggling to get the tasks seperated and then merged again...
    task0index = np.where(x[:,21] == 0.)[0]
    task1index = np.where(x[:,21] == 1.)[0]
    mean_task0 = mean[task0index]
    mean_task1 = mean[task1index]
    cov_task0 = cov[task0index]
    cov_task1 = cov[task1index]
    mean = np.column_stack([mean_task0,mean_task1])
    cov  = np.column_stack([cov_task0 ,cov_task1 ])
    #and now we are interested in the l2 norm of the mean and variance at each input location.
    return np.linalg.norm(mean, axis = 1) + a * np.linalg.norm(cov,axis = 1)


input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((23,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1, np.ones((23)), hps_bounds,
                                     init_dataset_size= 10, instrument_func = instrument, \
                                     acquisition_function=acq_func)


my_fvae.train()
my_fvae.go(N = 100, retrain_async_at=(), retrain_globally_at=(90,), retrain_locally_at=())

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
Suggested by gp

Suggested by gpCAM:  [ -0.7021277   -0.2336279    0.30476747   1.93657169   0.17110001
  -0.79963807  -0.2600306    2.56174584   0.52606738   1.37066404
  -2.68746769   1.34830255   0.38600203   0.33734207   4.70156109
 -19.6473366   11.05540755  23.89309666  19.82821456  -6.34782537
   6.52565207]
received:  [ 40.913754 -36.564117]

Suggested by gpCAM:  [ -0.41553242  -0.41074943  -0.45967167   1.9474534   -0.16131082
   0.11164873   0.44673879  -0.49872036   1.13063613   0.68430278
   3.55707234  -2.89231571   0.32200846   0.13810253 -37.65142314
   3.48149654 -11.7853069   26.05297654  25.19417887   9.66878791
 -32.03365111]
received:  [  6.796305 -52.875248]

Suggested by gpCAM:  [-6.74207000e-01 -6.68445418e-01 -1.82304890e-01  1.94756793e+00
  9.25273166e-01 -7.57601359e-01  1.61569246e-02  4.16488228e+00
  4.40766830e-03 -1.39172153e+00 -2.96603148e+00  1.23321037e+00
  4.22909831e-01 -1.36056761e-02 -1.15008568e+01 -1.91017677e+01
  7.16336059e+00  4.29302417e+01  3.18726991e+0

Suggested by gpCAM:  [ -0.38893359  -0.23692373   0.16560536   1.83871996   0.65051716
  -0.6095772    0.24965046  -4.24522153  -0.90742676   1.30552024
   1.15272916   2.02998361  -0.68995186   0.28415024 -33.18097141
   8.31254095 -10.65849036  12.53522243  -4.22953884  -0.78133947
 -30.98599095]
received:  [  5.412507 -25.124226]

Suggested by gpCAM:  [-3.64803021e-01 -2.10975434e-01 -2.53103362e-02  1.73577693e+00
  1.19629524e+00 -5.02795092e-01  7.65074137e-02  5.70433512e-01
 -1.59500558e+00  7.22149517e-01  1.70783154e+00 -5.71729461e-01
 -8.65775432e-01 -1.88771909e+00 -3.52235245e+01 -5.34590318e+00
  1.87165214e+01  1.67811274e+01  9.89837146e+00 -2.01310872e+01
 -1.69136115e+01]
received:  [-28.060942 -38.467083]

Suggested by gpCAM:  [-3.00846882e-01 -2.73039693e-01 -7.79782856e-02  1.13731774e+00
 -1.68898565e-01 -4.08249079e-01 -1.88698836e-02 -1.32658941e+00
 -6.76419411e-01  7.47745657e-01 -9.46000537e-01  9.98579112e-01
  7.61261169e-01 -1.49433361e+00 -2.90955243e+01

Suggested by gpCAM:  [ -0.80068625  -0.08636048   0.1277956    2.16926548   0.34030757
   0.22008074  -0.09538042  -4.47431441   1.2682593    0.20462085
  -2.81654686  -0.65531208  -1.8827655   -2.39899808 -34.28918092
  18.2221951   -2.5469851   16.19387822  28.2754336   -2.20577953
 -22.36131499]
received:  [-28.060942 -38.467083]

Suggested by gpCAM:  [ -0.55752133  -0.23054174  -0.11354435   1.7476799    0.06657902
  -0.39653461   0.40393115   0.99589735  -0.25714826  -2.80898885
  -3.40290716   1.86585784  -1.14015629  -0.24169912  -1.98997995
  -4.69397155  -1.71226193  21.38907879 -19.27159372 -19.62065965
 -27.4490613 ]
received:  [ 28.272627 -39.418568]

Suggested by gpCAM:  [ -0.14280889  -0.55765044  -0.44636783   1.9512346    1.16151903
  -0.04549708  -0.13814756  -2.13017418   0.95308796   1.35467439
  -0.2351355   -2.6017647    1.79327513   0.0408006  -23.03191617
  -2.27290341 -14.72700041   9.78397655 -11.52999122   7.37913918
 -34.60172612]
received:  [  0.407778 -32.8

Suggested by gpCAM:  [  0.46924457  -0.56033807  -0.18629247   0.86067195   0.4735911
  -0.62218265  -0.0213061   -1.07122949   0.84721717   1.8248198
   1.88421088  -1.97196365   0.5146325   -0.39770875   7.43738305
 -14.79680953 -13.57337467  20.7552349   -4.93445893   1.37232051
 -20.30306126]
received:  [ 34.797077 -37.787453]

Suggested by gpCAM:  [  0.535599    -0.79260207   0.10781796   1.42854183   0.3980126
  -0.03328664   0.55224955   2.2277383    0.45384696   0.62839793
  -3.32773429   1.01573336  -2.2194577   -0.44871071  -8.70735175
   5.62152852  14.09927209  23.15839182  31.70139307 -10.73707326
 -17.47716362]
received:  [  6.768624 -51.923767]

Suggested by gpCAM:  [  0.57579839  -0.75102982  -0.3946403    1.35352101   0.71069257
  -0.22808807   0.14741504   1.41021034   0.59707626  -1.9153677
   0.63683286   1.67024492  -1.45350431  -0.47629331  25.55112552
  19.18059143  12.50358645  40.52291785  25.7791832   14.58899741
 -23.50872463]
received:  [ 79.788612 -11.68964

## Plotting the 0th task in a 2d slice

In [48]:
x_pred = np.zeros((10000,22))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((22))
        x_pred[counter,[0,1,-1]] = np.array([x[i,j],y[i,j],0.])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)